In [2]:
import pandas as pd 
import plotly.express as px 
import numpy as np 
from sklearn.model_selection import train_test_split
pd.set_option('display.max_columns' , None)

In [3]:
# run this cell to update data 

df = pd.read_csv("data/todays_sessions.csv")
df = df[["userId", "Time", "Power (W)"]]

one_hot_users = pd.get_dummies(df["userId"])
df2 = df.drop("userId", axis=1)
df2 = df2.join(one_hot_users)
df2.set_index("Time", inplace=True, drop=True)
df2.index = pd.to_datetime(df2.index)

single_column = df2["Power (W)"]
temp = df2.drop(columns=["Power (W)"]).multiply(single_column, axis='index')
df2 = pd.concat([df2["Power (W)"], temp], axis=1)
df2.resample("1H").sum()

df2.to_csv("data/neural_netdata.csv")

userId                 Time  Power (W)
0     605  2020-11-05 00:00:00        0.0
1     605  2020-11-05 00:05:00        0.0
2     605  2020-11-05 00:10:00        0.0
3     605  2020-11-05 00:15:00        0.0
4     605  2020-11-05 00:20:00        0.0

In [6]:
import keras
import tensorflow

In [3]:
df2 = pd.read_csv("data/neural_netdata.csv")
df2.tail(50)

Time  Power (W)  455  486  491  506  589  603  605  \
753358  2023-02-22 19:50:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753359  2023-02-22 19:55:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753360  2023-02-22 20:00:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753361  2023-02-22 20:05:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753362  2023-02-22 20:10:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753363  2023-02-22 20:15:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753364  2023-02-22 20:20:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753365  2023-02-22 20:25:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753366  2023-02-22 20:30:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753367  2023-02-22 20:35:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753368  2023-02-22 20:40:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753369  2023-02-22 20:45:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753370  2023-02-22 20:50:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753371  2023-02-22 20:55:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753372  2023-02-22 21:00:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753373  2023-02-22 21:05:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753374  2023-02-22 21:10:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753375  2023-02-22 21:15:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753376  2023-02-22 21:20:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753377  2023-02-22 21:25:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753378  2023-02-22 21:30:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753379  2023-02-22 21:35:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753380  2023-02-22 21:40:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753381  2023-02-22 21:45:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753382  2023-02-22 21:50:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753383  2023-02-22 21:55:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753384  2023-02-22 22:00:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753385  2023-02-22 22:05:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753386  2023-02-22 22:10:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753387  2023-02-22 22:15:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753388  2023-02-22 22:20:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753389  2023-02-22 22:25:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753390  2023-02-22 22:30:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753391  2023-02-22 22:35:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753392  2023-02-22 22:40:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753393  2023-02-22 22:45:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753394  2023-02-22 22:50:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753395  2023-02-22 22:55:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753396  2023-02-22 23:00:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753397  2023-02-22 23:05:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753398  2023-02-22 23:10:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753399  2023-02-22 23:15:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753400  2023-02-22 23:20:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753401  2023-02-22 23:25:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753402  2023-02-22 23:30:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753403  2023-02-22 23:35:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753404  2023-02-22 23:40:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753405  2023-02-22 23:45:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753406  2023-02-22 23:50:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
753407  2023-02-22 23:55:00        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

        606  610  615  617  618  620  623  627  631  633  644  647  648  653  \
753358  0.0  0.

In [9]:
df2[["615"]].loc[df2.index > "2022-11"]

615
Time                    
2022-11-01 00:00:00  0.0
2022-11-01 00:05:00  0.0
2022-11-01 00:10:00  0.0
2022-11-01 00:15:00  0.0
2022-11-01 00:20:00  0.0
...                  ...
2023-02-22 23:35:00  0.0
2023-02-22 23:40:00  0.0
2023-02-22 23:45:00  0.0
2023-02-22 23:50:00  0.0
2023-02-22 23:55:00  0.0

[114624 rows x 1 columns]

In [21]:
df2[["615"]].loc[df2.index > "2023-01-16 18:00:00"].head(10)


615
Time                    
2023-01-16 18:05:00  0.0
2023-01-16 18:10:00  0.0
2023-01-16 18:15:00  0.0
2023-01-16 18:20:00  0.0
2023-01-16 18:25:00  0.0
2023-01-16 18:30:00  0.0
2023-01-16 18:35:00  0.0
2023-01-16 18:40:00  0.0
2023-01-16 18:45:00  0.0
2023-01-16 18:50:00  0.0

In [16]:
px.line(x=df2[["615"]].loc[df2.index > "2022-12"].index, y=df2[["615"]].loc[df2.index > "2022-12"]["615"]54)

In [2]:
df = pd.read_csv("data/raw_data.csv")
df = df[(df["peakPower_W"] > 0) & (df["cumEnergy_Wh"] > 0)]

In [7]:
abc = df.copy(deep=True)
abc["connectTime"] = pd.to_datetime(df["connectTime"])
abc["connectTime"] = abc["connectTime"].dt.hour
abc

Unnamed: 0  vehicle_maxChgRate_W  peakPower_W  sch_centsPerHr  \
0              0                  8800         3380           150.0   
1              1                  6600         6563           250.0   
2              2                170000         6822           250.0   
3              3                  3600         3442           142.0   
4              4                170000         5170           250.0   
...          ...                   ...          ...             ...   
3133        3133                 50000          919           250.0   
3134        3134                  4500         3833             NaN   
3135        3135                  3600         3444            50.0   
3136        3136                  4250         3239           127.0   
3137        3137                  6600         6163           213.0   

      connectTime                    user_email   vehicle_model  \
0               6        lamartell@berkeley.edu     Prius Prime   
1              10           erfanm@berkeley.edu    Clarity PHEV   
2              22        amehregan@berkeley.edu         Model 3   
3              15          nthaman@berkeley.edu            Volt   
4               9         scott.moura@gmail.com         Model 3   
...           ...                           ...             ...   
3133            6           k.moua@berkeley.edu  Ioniq Electric   
3134            9  lauryn.holloway@berkeley.edu         Model 3   
3135           10          nthaman@berkeley.edu            Volt   
3136           21     mwhitwill107@berkeley.edu            Volt   
3137           11           erfanm@berkeley.edu    Clarity PHEV   

             Duration  userId  regular             Deadline  \
0     0 days 01:40:50     603        0  2022-01-07T08:15:00   
1     0 days 01:53:35     793        1                  NaN   
2     0 days 00:56:17     902        1                  NaN   
3     0 days 04:26:19     804        1                  NaN   
4     0 days 06:37:26     615        1                  NaN   
...               ...     ...      ...                  ...   
3133  0 days 02:35:05     964        1                  NaN   
3134  0 days 07:11:45    1126        1                  NaN   
3135  0 days 05:09:48     804        0  2021-10-14T15:30:00   
3136  0 days 00:47:04    1154        0  2022-06-05T09:15:00   
3137  0 days 00:50:52     793        1                  NaN   

          startChargeTime  sch_centsPerOverstayHr  sch_centsPerKwh     choice  \
0     2022-01-07T06:24:19                   500.0              0.0  SCHEDULED   
1     2022-10-20T10:16:33                   400.0              0.0    REGULAR   
2     2023-02-02T22:08:51                   400.0              0.0    REGULAR   
3     2022-03-23T10:03:50                   400.0              0.0    REGULAR   
4     2022-06-24T09:57:41                   400.0              0.0    REGULAR   
...                   ...                     ...              ...        ...   
3133  2022-10-06T06:45:09                   400.0              0.0    REGULAR   
3134  2022-10-13T09:08:29                     NaN              NaN    REGULAR   
3135  2021-10-14T10:10:20                   400.0              0.0  SCHEDULED   
3136  2022-06-04T21:33:03                   400.0              0.0  SCHEDULED   
3137  2022-04-08T11:59:16                   400.0              0.0    REGULAR   

      siteId   estCost                                      slrpPaymentId  \
0         25   3.26708  8021073541d47f523b5c018e82e34477ef6fc0f04610cd...   
1         25   3.09348  46fd620dfb0f65509d36c93ced73d167268ade266ecb18...   
2         25   1.78513  40aa08c906ce9403a383ba4142ad4784d6af32df1e3dd4...   
3         25   6.22580  1178d775901330553b8f1002dbfd65fc96e0a35a9a22e8...   
4         25   9.57472  677481c9cf67f6563f944c9e44357b5e4a30925ef8a0b7...   
...      ...       ...                                                ...   
3133      25   4.14445  54e801e6c08028f3ca182e3f9d7d6807d0cbcb7823aefe...   
31

In [8]:
px.histogram(data_frame=abc, x = "connectTime", nbins = 24)